## Import Libraries

In [1]:
import os
import cv2
import math
import random
import numpy as np
import tensorflow as tf
from moviepy.editor import *

from tensorflow.keras.models import load_model

## Variables

In [2]:
model_output_size = 101
image_height = 64
image_width = 64
classes_list = os.listdir('UCF101')


## Creating Directory

In [3]:
# Creating The Output directories if it does not exist
output_directory = 'Youtube_Videos'
os.makedirs(output_directory, exist_ok = True)

## Downloading YouTube Video

In [4]:
from pytube import YouTube

# link of the video to be downloaded
link='https://www.youtube.com/watch?v=ifaZ1BsSIhg'
video_title = 'TestVideo'

yt = YouTube(link)

yt.streams.filter(file_extension='mp4')




[<Stream: itag="18" mime_type="video/mp4" res="360p" fps="30fps" vcodec="avc1.42001E" acodec="mp4a.40.2" progressive="True" type="video">, <Stream: itag="22" mime_type="video/mp4" res="720p" fps="30fps" vcodec="avc1.64001F" acodec="mp4a.40.2" progressive="True" type="video">, <Stream: itag="136" mime_type="video/mp4" res="720p" fps="30fps" vcodec="avc1.64001f" progressive="False" type="video">, <Stream: itag="135" mime_type="video/mp4" res="480p" fps="30fps" vcodec="avc1.4d400c" progressive="False" type="video">, <Stream: itag="134" mime_type="video/mp4" res="360p" fps="30fps" vcodec="avc1.4d401e" progressive="False" type="video">, <Stream: itag="133" mime_type="video/mp4" res="240p" fps="30fps" vcodec="avc1.4d400c" progressive="False" type="video">, <Stream: itag="160" mime_type="video/mp4" res="144p" fps="30fps" vcodec="avc1.4d400b" progressive="False" type="video">, <Stream: itag="139" mime_type="audio/mp4" abr="48kbps" acodec="mp4a.40.5" progressive="False" type="audio">, <Stream: 

In [5]:
stream = yt.streams.get_by_itag(22)

path = stream.download(output_directory,video_title)


## Test

In [6]:
def make_average_predictions(video_file_path, predictions_frames_count):
    
    # add model name
    model = load_model('101Model___Date_Time_2021_12_28__07_18_09___Loss_0.5102582573890686___Accuracy_0.8626126050949097.h5')
    
    # Initializing the Numpy array which will store Prediction Probabilities
    predicted_labels_probabilities_np = np.zeros((predictions_frames_count, model_output_size), dtype = np.float)

    # Reading the Video File using the VideoCapture Object
    video_reader = cv2.VideoCapture(video_file_path)

    # Getting The Total Frames present in the video 
    video_frames_count = int(video_reader.get(cv2.CAP_PROP_FRAME_COUNT))
    
    # Calculating The Number of Frames to skip Before reading a frame
    skip_frames_window = video_frames_count // predictions_frames_count

    for frame_counter in range(predictions_frames_count): 

        # Setting Frame Position
        video_reader.set(cv2.CAP_PROP_POS_FRAMES, frame_counter * skip_frames_window)

        # Reading The Frame
        _ , frame = video_reader.read() 

        # Resize the Frame to fixed Dimensions
        resized_frame = cv2.resize(frame, (image_height, image_width))
        
        # Normalize the resized frame by dividing it with 255 so that each pixel value then lies between 0 and 1
        normalized_frame = resized_frame / 255

        # Passing the Image Normalized Frame to the model and receiving Predicted Probabilities.
        predicted_labels_probabilities = model.predict(np.expand_dims(normalized_frame, axis = 0))[0]

        # Appending predicted label probabilities to the deque object
        predicted_labels_probabilities_np[frame_counter] = predicted_labels_probabilities

    # Calculating Average of Predicted Labels Probabilities Column Wise 
    predicted_labels_probabilities_averaged = predicted_labels_probabilities_np.mean(axis = 0)

    # Sorting the Averaged Predicted Labels Probabilities
    predicted_labels_probabilities_averaged_sorted_indexes = np.argsort(predicted_labels_probabilities_averaged)[::-1]

    # Iterating Over All Averaged Predicted Label Probabilities
    for predicted_label in predicted_labels_probabilities_averaged_sorted_indexes:

        # Accessing The Class Name using predicted label.
        predicted_class_name = classes_list[predicted_label]

        # Accessing The Averaged Probability using predicted label.
        predicted_probability = predicted_labels_probabilities_averaged[predicted_label]

        print(f"CLASS NAME: {predicted_class_name}   AVERAGED PROBABILITY: {(predicted_probability*100):.2}")
    
    # Closing the VideoCapture Object and releasing all resources held by it. 
    video_reader.release()

In [7]:
#Calling The Make Average Method To Start The Process
make_average_predictions(path, 50)

# Play Video File in the Notebook
VideoFileClip(path).ipython_display(width = 700)

CLASS NAME: Rafting   AVERAGED PROBABILITY: 4.5e+01
CLASS NAME: FloorGymnastics   AVERAGED PROBABILITY: 1.8e+01
CLASS NAME: IceDancing   AVERAGED PROBABILITY: 1.1e+01
CLASS NAME: Surfing   AVERAGED PROBABILITY: 9.9
CLASS NAME: UnevenBars   AVERAGED PROBABILITY: 5.1
CLASS NAME: Skiing   AVERAGED PROBABILITY: 3.3
CLASS NAME: BalanceBeam   AVERAGED PROBABILITY: 2.2
CLASS NAME: SumoWrestling   AVERAGED PROBABILITY: 1.3
CLASS NAME: SkyDiving   AVERAGED PROBABILITY: 0.9
CLASS NAME: BasketballDunk   AVERAGED PROBABILITY: 0.89
CLASS NAME: Billiards   AVERAGED PROBABILITY: 0.72
CLASS NAME: Kayaking   AVERAGED PROBABILITY: 0.46
CLASS NAME: Shotput   AVERAGED PROBABILITY: 0.43
CLASS NAME: MilitaryParade   AVERAGED PROBABILITY: 0.27
CLASS NAME: FrontCrawl   AVERAGED PROBABILITY: 0.1
CLASS NAME: PommelHorse   AVERAGED PROBABILITY: 0.033
CLASS NAME: CuttingInKitchen   AVERAGED PROBABILITY: 0.029
CLASS NAME: CliffDiving   AVERAGED PROBABILITY: 0.028
CLASS NAME: Typing   AVERAGED PROBABILITY: 0.018
CL

t:   0%|                                                                             | 0/151 [00:00<?, ?it/s, now=None]

Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3
MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4
